<a href="https://colab.research.google.com/github/Naveen-Chaurasia/Generative-AI-POCs/blob/main/ChatwithPdf_Mixtral8x7B.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [5]:
!pip install farm-haystack[colab]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 856.0/856.0 kB 7.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.0/75.0 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 16.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.7/48.7 kB 5.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.8/10.8 MB 50.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 49.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 68.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.3/4.3 MB 78.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 66.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [6]:

from getpass import getpass
HF_TOKEN = getpass("Il Tuo Hugging Face Token")



Il Tuo Hugging Face Token··········


In [7]:
from haystack.nodes import PreProcessor,PromptModel, PromptTemplate, PromptNode

In [8]:
from google.colab import files
files.upload()

Saving Sustain360 User_Guide121223.pdf to Sustain360 User_Guide121223 (1).pdf


{'Sustain360 User_Guide121223 (1).pdf': b'%PDF-1.7\n%\xc2\xb3\xc7\xd8\r\n3 0 obj\r<</Author (google1580233541) /Comments () /Company () /CreationDate (D:20231213205054+20\'50\') /Creator (WPS Writer) /Keywords () /ModDate (D:20231213205054+20\'50\') /Producer () /SourceModified (D:20231213205054+20\'50\') /Subject () /Title () /Trapped /False>>\rendobj\r9 0 obj\r<</BitsPerComponent 8 /ColorSpace /DeviceGray /Filter /FlateDecode /Height 1120 /Length 899 /Matte [0 0 0] /Subtype /Image /Type /XObject /Width 805>>\r\nstream\r\nx\x9c\xed\xc11\x01\x00\x00\x0c\x02\xa0\xf5/\xed\x1a\xf8\xfa\x00\t\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x

In [9]:
%%capture
!pip install PyPDF2

In [10]:
import PyPDF2
from haystack import Document

pdf_file_path = "/content/Sustain360 User_Guide121223.pdf"  # Sostituisci con il percorso del tuo file PDF

def extract_text_from_pdf(pdf_path):
    text = ""
    with open(pdf_path, "rb") as pdf_file:
        pdf_reader = PyPDF2.PdfReader(pdf_file)
        for page_num in range(len(pdf_reader.pages)):
            page = pdf_reader.pages[page_num]
            text += page.extract_text()

    return text

pdf_text = extract_text_from_pdf(pdf_file_path)

# Creazione del documento di Haystack
doc = Document(
    content=pdf_text,
    meta={"pdf_path": pdf_file_path}
)


In [11]:
docs = [doc]

processor = PreProcessor(
    clean_empty_lines=True,
    clean_whitespace=True,
    clean_header_footer=True,
    split_by="word",
    split_length=500,
    split_respect_sentence_boundary=True,
    split_overlap=0,
    language="it",
)

# Processa la lista di documenti
preprocessed_docs = processor.process(docs)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
Preprocessing: 100%|██████████| 1/1 [00:00<00:00, 32.48docs/s]


In [13]:
preprocessed_docs[1]

<Document: {'content': '.g.GWP).2.4)CompareSubstitutes:Itwill\ncreateabarchartshowingusthedifferencebetweentheKPIvariable(e.g.GWP)wehave\nselectedfordifferentsubstitutesofthechemical.\n5.RecommendationEngine:6.CarbonReport:WhenutilizingSustain360°™,thecarbonreportoptionscanbe\nincorporatedintotheassessmenttocalculatethenetemissionsaccountingfordifferentlife\ncycleprocess.Thisallowsforamorecomprehensiveunderstandingoftheenvironmental\nimpactofaproductorprocessandhelpsidentifyopportunitiesforemissionreductionand\noffsetting.\n1.Optionsdropdown:Wecanselectonedesignoptionpresentinprojectforwhichwe\nwanttofindthecarbonreport.\n2.EnvironmentalMetricsDrop-down:fromthisdropdownwecanselectthekpifor\nwhichwewanttoseetheheat-mapforaselecteddesignoption.\n3.Scopes:Fromscopeswecanselectthescopesforwhichwewanttoseethecarbon\nreport\n4.Carbonreportheat-map:Itisusedforvisualizingthecarbonreportandtofindout\nmaterialswhichisaccountingformorecarbonemissionthroughheatmap.\n7.EnvironmentalGPT(plannedforre

In [14]:
from haystack.document_stores import InMemoryDocumentStore

document_store = InMemoryDocumentStore(use_bm25=True)
document_store.write_documents(preprocessed_docs)

Updating BM25 representation...: 100%|██████████| 2/2 [00:00<00:00, 1264.87 docs/s]


In [15]:
from haystack import Pipeline
from haystack.nodes import BM25Retriever
retriever = BM25Retriever(document_store, top_k=2)

In [16]:
qa_template = PromptTemplate(prompt=
  """ Using exclusively the information contained in the context,
  respond solely to the posed question without adding suggestions of possible questions and answer exclusively in Italian.
  If the answer cannot be deduced from the context, respond: "\ I wouldn't know because it's not relevant to the Context.\"
  Context: {join(documents)};
  Question: {query}
  """)

In [17]:
# Ora puoi utilizzare http_client per le tue richieste HTTP, compresa l'inizializzazione di PromptNode
prompt_node = PromptNode(
    model_name_or_path="mistralai/Mixtral-8x7B-Instruct-v0.1",
    api_key=HF_TOKEN,
    default_prompt_template=qa_template,
    max_length=500,
    model_kwargs={"model_max_length": 5000}
)

In [18]:
rag_pipeline = Pipeline()
rag_pipeline.add_node(component=retriever, name="retriever", inputs=["Query"])
rag_pipeline.add_node(component=prompt_node, name="prompt_node", inputs=["retriever"])

In [19]:
from pprint import pprint
print_answer = lambda out: pprint(out["results"][0].strip())

In [22]:
print_answer(rag_pipeline.run(query="What Are advanced anlaytics options?"))

('and\n'
 'PhotochemicalOxidationPotential(POCP).Thesemetricsprovidevaluableinsightsintothe\n'
 'environmentalimpactsoftheproduct,process,orsystemunderanalysis.\n'
 '3.Visualization:VisualizationofLifeCycleAssessmentresultsallowsuserstogainadeeper\n'
 'understandingofsystemrelationshipsandimpactswithinaninteractiveplatform.\n'
 '4.LifeCycleAssessmentDatabase:TheLifeCycleAssessmentdatabasecontainsinformation\n'
 'abouttheenvironmentalimpactsoftheproduct,process,orsystemunderanalysis.Thisdatabase\n'
 'isintegratedwiththeSustain360°™platform,allowingforcomprehensiveanalysisand\n'
 'visualizationoflifecycleassessmentresults.\n'
 '6.CarbonFootprint:Carbonfootprintrepresentsthetotalamountofgreenhousegasemissions\n'
 'generatedbyanorganization,product,ormanufacturingprocess.Itisusuallymeasured\n'
 'inunitsofcarbon '
 'dioxideequivalents(CO2e).Carbonfootprintanalysishelpsstakeholders\n'
 "understandtheclimatechangeimpactofanorganization'soperationsandprovides\n"
 'valuableinsightsintotheeffect